In [1]:
import sys
sys.path.append("../source")

from Match_Analytics import Match
from Tracking_Visualization import draw_pitch
from Tracking_Constants import *
import numpy as np

In [2]:
match_1 = Match(data_source = 'metrica-sports', match_id = 1, name = "Sample_Game_1", field_dimen=(106., 68.))

Reading team: home
Reading team: away


In [3]:
match_1.tracking_home

Period  Time [s]  Home_11_x  Home_11_y  Home_1_x  Home_1_y  Home_2_x  \
Frame                                                                          
1            1      0.04    0.00082    0.48238   0.32648   0.65322   0.33701   
2            1      0.08    0.00096    0.48238   0.32648   0.65322   0.33701   
3            1      0.12    0.00114    0.48238   0.32648   0.65322   0.33701   
4            1      0.16    0.00121    0.48238   0.32622   0.65317   0.33687   
5            1      0.20    0.00129    0.48238   0.32597   0.65269   0.33664   
...        ...       ...        ...        ...       ...       ...       ...   
145002       2   5800.08    0.90614    0.45355       NaN       NaN   0.34157   
145003       2   5800.12    0.90550    0.45355       NaN       NaN   0.34127   
145004       2   5800.16    0.90492    0.45355       NaN       NaN   0.34089   
145005       2   5800.20    0.90456    0.45356       NaN       NaN   0.34056   
145006       2   5800.24    0.90456    0.45356       NaN       NaN   0.33996   

        Home_2_y  Home_3_x  Home_3_y  ...  Home_10_x  Home_10_y  Home_12_x  \
Frame                                 ...                                    
1        0.48863   0.30927   0.35529  ...    0.55243    0.43269        NaN   
2        0.48863   0.30927   0.35529  ...    0.55243    0.43269        NaN   
3        0.48863   0.30927   0.35529  ...    0.55243    0.43269        NaN   
4        0.48988   0.30944   0.35554  ...    0.55236    0.43313        NaN   
5        0.49018   0.30948   0.35528  ...    0.55202    0.43311        NaN   
...          ...       ...       ...  ...        ...        ...        ...   
145002   0.64598   0.31228   0.67513  ...        NaN        NaN    0.30044   
145003   0.64583   0.31230   0.67529  ...        NaN        NaN    0.30044   
145004   0.64569   0.31214   0.67501  ...        NaN        NaN    0.30044   
145005   0.64552   0.31171   0.67468  ...        NaN        NaN    0.30044   
145006   0.64544   0.31122   0.67532  ...        NaN        NaN    0.30044   

        Home_12_y  Home_13_x  Home_13_y  Home_14_x  Home_14_y   ball_x  \
Frame                                                                    
1             NaN        NaN        NaN        NaN        NaN  0.45472   
2             NaN        NaN        NaN        NaN        NaN  0.49645   
3             NaN        NaN        NaN        NaN        NaN  0.53716   
4             NaN        NaN        NaN        NaN        NaN  0.55346   
5             NaN        NaN        NaN        NaN        NaN  0.55512   
...           ...        ...        ...        ...        ...      ...   
145002    0.68311    0.33644    0.65390    0.34157    0.64598      NaN   
145003    0.68311    0.33656    0.65398    0.34127    0.64583      NaN   
145004    0.68311    0.33637    0.65366    0.34089    0.64569      NaN   
145005    0.68311    0.33615    0.65317    0.34056    0.64552      NaN   
145006    0.68311    0.33563    0.65166    0.33996    0.64544      NaN   

         ball_y  
Frame            
1       0.38709  
2       0.40656  
3       0.42556  
4       0.42231  
5       0.40570  
...         ...  
145002      NaN  
145003      NaN  
145004      NaN  
145005      NaN  
145006      NaN  

[145006 rows x 32 columns]

In [145]:
N = 1

match_1.preprocess()

histogram2d, histx, histy = np.histogram2d(match_1.tracking_home['Home_11_y'],
                                             match_1.tracking_home['Home_11_x'], 
                                             bins = [int(match_1.field_dimen[1]*N),
                                                     int(match_1.field_dimen[0]*N)],
                                             range = [[-match_1.field_dimen[1]/2,match_1.field_dimen[1]/2],
                                                      [-match_1.field_dimen[0]/2,match_1.field_dimen[0]/2]],
                                             
                                             density = True)

In [155]:
from bokeh.io import show, output_notebook
from bokeh.plotting import figure
from bokeh.palettes import Greens256
from bokeh.util.hex import hexbin
from bokeh.transform import linear_cmap
from numpy.linalg import eig
output_notebook()

p = draw_pitch(grass_alpha=0, line_color='green', background_fill_color= "white")

p.image(image=[-histogram2d],
        x=-match_1.field_dimen[0]/2,
        y=-match_1.field_dimen[1]/2,
        dw=match_1.field_dimen[0],
        dh=match_1.field_dimen[1],
        palette=Greens256,
        level="image",
        alpha = 0.5)

players = ['Home_1', 'Home_2', 'Home_3','Home_4','Home_5','Home_6','Home_7','Home_8','Home_9','Home_10','Home_11', 'Home_12', "ball"]
colors = ['blue', 'blue', 'blue','red','blue','blue','blue','blue','blue','blue','blue', 'blue', 'black']

x_means = [match_1.tracking_home[player+'_x'].mean() for player in players]
y_means = [match_1.tracking_home[player+'_y'].mean() for player in players]

cov_matrices = [match_1.tracking_home[[player+'_x',player+'_y']].cov() for player in players]

values, vectors = eig(cov_matrices)

angles = np.arctan(vectors[:,0,1]/vectors[:,0,0])

x_std = [match_1.tracking_home[player+'_x'].std() for player in players]
y_std = [match_1.tracking_home[player+'_y'].std() for player in players]

p.circle(x_means,
         y_means,
         size=10,
         color=colors,
         alpha=1)

p.ellipse(x=x_means, 
          y=y_means, 
          width=x_std, 
          height=y_std,
          fill_color = None,
          line_width = 2,
          angle = angles)

show(p)

Loading BokehJS ...

In [141]:
vectors[:,0,1]

array([-0.03165644,  0.16688749,  0.05596132, -0.09700768,  0.23979891,
       -0.0811234 ,  0.51724191, -0.28728296,  0.032221  , -0.47502817,
       -0.00378693,  0.18039056,  0.14550107])